In [ ]:
import datetime
import pandas.tseries.offsets as off
import globeop_reports as go
import pandas as pd
import matplotlib.pyplot as plt

from db import dbengine
engine  = dbengine('dawndb')

In [ ]:
#PNL Allocation
report_date = datetime.date.today() - off.MonthEnd(1)
report_date

In [ ]:
pnl_alloc = go.alloc('pnl')
alloc = pnl_alloc.xs(report_date)

In [ ]:
#Prev monthend PNL Allocation
go.pnl_alloc_plot(alloc)

In [ ]:
#Pnl Alloc through time
pnl_alloc_sum = pnl_alloc['mtdtotalbookpl']/ pnl_alloc['mtdtotalbookpl'].groupby(['periodenddate']).sum()
pnl_alloc_sum.unstack().plot(kind='bar')

In [ ]:
#Capital Allocation
cap_alloc = go.alloc('capital')
alloc1 = cap_alloc.xs(report_date)
go.cap_alloc_plot_pie(alloc1)

In [ ]:
#Average Portfolio Sales Turnover - as of last monthend from today
go.avg_turnover()

In [ ]:
#Number of bond positions by strategy by month - and copy to clipboard
#go.num_bond_by_strat()

In [ ]:
#Number of bond trades by direction by month - and copy to clipboard
#go.num_bond_trades()

In [ ]:
df = cap_alloc.endbooknav.groupby('periodenddate').apply(lambda x: x/x.sum())
df = df.unstack().groupby(pd.Grouper(freq='M')).apply(lambda df: df.loc[df.index[-1]])
df = go.shift_cash(datetime.date(2017,11,30), -2096454, df, 'Curve')
temp = df.iloc[-1].sort_values(ascending=False)
df = df.reindex(temp.index, axis=1)

In [ ]:
ax = go.cap_alloc_plot_bar(df[:-1])
lgd = ax.legend(loc='lower center', bbox_to_anchor=(0.5, -0.3), ncol=4)
ax.figure.savefig("/home/serenitas/edwin/PythonGraphs/cap_alloc_1.png", bbox_extra_artists=(lgd,), bbox_inches='tight')

In [ ]:
#This takes a while
df = go.get_rmbs_pos_df()

In [ ]:
#Plot Duration and Yield to Maturity of RMBS Portfolio
#Filtering out RMBS Bonds:
#df = df[df.strat != 'MTG_FP']
bond_dur, bond_yield = {}, {}
for d, g in df.groupby(pd.Grouper(freq='M')):
        bond_dur[d] = sum(g.curr_ntl * g[('moddur', 3)])/sum(g.curr_ntl)
        bond_yield[d] = sum(g.endlocalmv * g[('moddur', 3)] * g.b_yield) /sum(g.endlocalmv * g[('moddur', 3)])
a = pd.Series(bond_dur)
b = pd.Series(bond_yield)
a.name = 'Duration'
b.name = 'Yield-to-maturity'

fig = plt.figure()
ax0 = fig.add_subplot(111)
ax1 = ax0.twinx()

a.plot(kind='line', color = 'r', ax=ax0, label = a.name, legend=True)
b.plot(kind='line', secondary_y=True, ax=ax1, label = b.name, legend=True)

ax1.set_xlabel('date')
ax1.set_xlim([a.index.min(), a.index.max()])
ax0.set_ylabel('Duration')
ax1.set_ylabel('Yield-to-Maturity')

ax0.legend(loc=2)
fig.tight_layout()

In [ ]:
#Calculate Average Holding Period of RMBS portfolio
sql_string = "SELECT * FROM bonds where buysell= True"
df_trades = pd.read_sql_query(sql_string, dbengine('dawndb'), parse_dates={'lastupdate': {'utc': True}, 'trade_date': {}, 'settle_date': {}})
df_trades['trade_date2'] = df_trades['trade_date']
#df_trades = df_trades.groupby(['identifier']).last()
#df_with_trades = df.reset_index().merge(df_trades.reset_index(), on='identifier')
df_with_trades = pd.merge_asof(df.sort_index(), df_trades.set_index('trade_date').sort_index(), 
                               left_index=True,
                               right_index=True,
                               left_by='identifier',
                               right_by='cusip')
df_with_trades['hold'] = (df_with_trades.index - df_with_trades.trade_date2).dt.days/365
sp = {}
for i, g in df_with_trades.groupby('periodenddate'):
    sp[i] = sum(g.endbooknav * g.hold)/sum(g.endbooknav)
holding_period = pd.DataFrame.from_dict(sp, orient='index')
ax = holding_period.plot(legend=False, title='Average Holding Period')
ax.set_xlabel('date')
ax.set_ylabel('Years')